# Exam

Develop a model for predicting review rating.  
**Multiclass classification into 5 classes**  
Score: **F1 with macro averaging**  
You are forbidden to use test dataset for any kind of training.  
Remember proper training pipeline.  
If you are not using default params in the models, you have to use some validation scheme to justify them. 

Use `random_state` or `seed` params - your experiment must be reprodusible.


### 1 baseline = 0.51
### 2 baseline = 0.53


In [0]:
import pandas as pd
import numpy as np

In [0]:
import torch
import torch.nn as nn
import torch.optim as optim
import torch.nn.functional as F
from torch.utils.data import DataLoader, TensorDataset
from tqdm import tqdm_notebook as tqdm
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn import metrics
from sklearn.model_selection import train_test_split

In [0]:
RANDOM_STATE = 42
DEVICE = 'cuda'

In [4]:
!unzip "exam_data.zip"

Archive:  exam_data.zip
replace test.csv? [y]es, [n]o, [A]ll, [N]one, [r]ename: y
  inflating: test.csv                
replace train.csv? [y]es, [n]o, [A]ll, [N]one, [r]ename: A
  inflating: train.csv               


In [5]:
df_train = pd.read_csv('train.csv')
df_test = pd.read_csv('test.csv')
df_train.shape, df_test.shape

((48192, 3), (5355, 3))

In [0]:
df_train['text'] = df_train['title'] + '. ' + df_train['review']
df_test['text'] = df_test['title'] + '. ' + df_test['review']

In [7]:
df_train.head()

review  ...                                               text
0  The staff was very friendly, the breakfast ver...  ...  Walker Gem. The staff was very friendly, the b...
1  Excellent service - very approachable and prof...  ...  Excellent Service. Excellent service - very ap...
2  Really a top notch place to spend a day at the...  ...  Good location, warm and friendly staff. Really...
3  a little noisy, there was a false fire alarm a...  ...  nice hotel,. a little noisy, there was a false...
4  Place had too many animals and I'm allergic to...  ...  Experience. Place had too many animals and I'm...

[5 rows x 4 columns]

In [0]:
X_train, y_train = df_train.loc[:, df_train.columns == 'text'], df_train.loc[:, df_train.columns == 'target']
X_test, y_test = df_test.loc[:, df_test.columns == 'text'], df_test.loc[:, df_test.columns == 'target']

In [0]:
tfidf = TfidfVectorizer(min_df=3)  # , min_df=10
X_train = tfidf.fit_transform(np.array(X_train).reshape(-1,))

In [0]:
X_test = tfidf.transform(np.array(X_test).reshape(-1,))

In [11]:
X_train.shape, X_test.shape

((48192, 16309), (5355, 16309))

In [0]:
EMBEDDING_SIZE = X_train.shape[1]

In [13]:
y_train['target'] -= 1
y_test['target'] -= 1

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.
/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


In [0]:
class LogRegNN(nn.Module):
    
    def __init__(self, n_features, n_classes):
        super().__init__()
        
        # create tensor of weights and tensor of biases
        # initialize tensors from N(0,1) 
        # W has shape (n_features, n_classes)
        # b has shape (n_classes,)
        self.W = nn.Parameter(torch.randn(n_features, n_classes))
        self.b = nn.Parameter(torch.randn(n_classes))
        
    def forward(self, x):
        """
        In this method we implement connections between neural network weights
        x: batch feature matrix
        returns: probability logits
        """
        result = torch.mm(x, self.W) + self.b
        return result

In [0]:
def train_batch(model, batch_x, batch_y):
    # set NN model in training mode
    model.train()
    
    # zero gradients
    optimizer.zero_grad()
    # forward pass
    pred = model(batch_x)
    # cross-entropy loss
    loss = criterion(pred, batch_y)
    # calculate gradients
    loss.backward()
    # make optimization step
    optimizer.step()
    
    # return batch loss
    return loss.data.detach().item()

def eval_batch(model, batch_x, batch_y):
    # set NN model in evaluation mode
    model.eval()
    
    with torch.no_grad():
        # forward pass
        pred = model(batch_x)
        # cross-entropy loss
        loss = criterion(pred, batch_y)

    # return batch loss
    return loss.data.item()

In [0]:
def train(model, train_loader, valid_loader, n_epochs, early_stopping_patience=5):
    """
    early_stopping_patience - number of consecutive epochs of growing validation loss to wait
    """
    history = {'train': [], 'valid': []}

    num_of_val_loss_growths = 0
    prev_val_loss = np.inf

    for epoch in range(n_epochs):
        epoch_train_loss = 0
        
        # iterate over batches
        for batch_x, batch_y in tqdm(train_loader, desc=f'epoch:{epoch}', leave=True):

            loss = train_batch(model, batch_x, batch_y)
            epoch_train_loss += loss

        # average loss for epoch
        epoch_train_loss /= len(train_loader)
        history['train'].append(epoch_train_loss)
        
        epoch_valid_loss = 0
        for batch_x, batch_y in valid_loader:
            loss = eval_batch(model, batch_x, batch_y)
            epoch_valid_loss += loss
            
        epoch_valid_loss /= len(valid_loader)

        if epoch_valid_loss > prev_val_loss:
            num_of_val_loss_growths += 1
        else:
            num_of_val_loss_growths = 0
            prev_val_loss = epoch_valid_loss

        print(f'train loss: {epoch_train_loss:.3f} valid loss:{epoch_valid_loss:.3f}')
        history['valid'].append(epoch_valid_loss)

        if num_of_val_loss_growths == early_stopping_patience:
            print(f'early stopping! best valid loss: {prev_val_loss}')
            break

    return history

In [0]:
def predict(model, test_loader):
    
    model.eval()
    
    result = []
    with torch.no_grad():
        for batch_x in test_loader:
            pred = torch.argmax(F.softmax(model(batch_x), dim=1), dim=1)
            result.append(pred)
    return np.concatenate(result)

In [40]:
X_train.shape, y_train.shape

((48192, 16309), (48192, 1))

In [0]:
X_train2, X_valid2, y_train2, y_valid2 = train_test_split(X_train, y_train, stratify=y_train,
                                                      shuffle=True, test_size=0.3, random_state=RANDOM_STATE)

In [42]:
X_train2.shape, X_valid2.shape

((33734, 16309), (14458, 16309))

In [0]:
batch_size = 512


train_loader = DataLoader(TensorDataset(torch.tensor(X_train2.todense()).float(), torch.tensor(np.array(y_train2).reshape(-1,)).long()), 
                          batch_size=batch_size, shuffle=True)
valid_loader = DataLoader(TensorDataset(torch.tensor(X_valid2.todense()).float(), torch.tensor(np.array(y_valid2).reshape(-1,)).long()), 
                          batch_size=batch_size)
test_loader = DataLoader(torch.tensor(X_test.todense()).float(), 
                          batch_size=batch_size)

In [0]:
NUM_CLASSES = 5

model = LogRegNN(EMBEDDING_SIZE, NUM_CLASSES)

In [45]:
criterion = nn.CrossEntropyLoss()
# L2 regularization is embeded in 
optimizer = optim.SGD(model.parameters(), lr=0.5, weight_decay=0.0001)

train(model, train_loader, valid_loader, 20, -1);

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:14: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  



train loss: 1.737 valid loss:1.675



train loss: 1.667 valid loss:1.647



train loss: 1.640 valid loss:1.621



train loss: 1.614 valid loss:1.598


...


train loss: 1.415 valid loss:1.414



train loss: 1.404 valid loss:1.404



train loss: 1.393 valid loss:1.393



train loss: 1.383 valid loss:1.384



train loss: 1.373 valid loss:1.375


In [46]:
train(model, train_loader, valid_loader, 80, -1);

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:14: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  



train loss: 1.364 valid loss:1.367



train loss: 1.355 valid loss:1.358



train loss: 1.346 valid loss:1.350



train loss: 1.338 valid loss:1.343


...


train loss: 1.077 valid loss:1.112



train loss: 1.075 valid loss:1.111



train loss: 1.074 valid loss:1.110



train loss: 1.072 valid loss:1.108



train loss: 1.070 valid loss:1.107


In [0]:
from sklearn.metrics import f1_score

def count_f1_score():
    y_pred = predict(model, test_loader)
    f1_score_ = f1_score(y_test, y_pred, average='macro')
    return f1_score_

In [48]:
count_f1_score()

0.4271157232434272

In [49]:
train(model, train_loader, valid_loader, 100, 5);

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:14: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  



train loss: 1.069 valid loss:1.106



train loss: 1.067 valid loss:1.104



train loss: 1.066 valid loss:1.103



train loss: 1.064 valid loss:1.101


...


train loss: 0.978 valid loss:1.032



train loss: 0.977 valid loss:1.031



train loss: 0.977 valid loss:1.031



train loss: 0.976 valid loss:1.030



train loss: 0.976 valid loss:1.030


In [50]:
count_f1_score()

0.4707026244936163

In [51]:
train(model, train_loader, valid_loader, 100, 5);

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:14: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  



train loss: 0.975 valid loss:1.029



train loss: 0.974 valid loss:1.029



train loss: 0.974 valid loss:1.029



train loss: 0.973 valid loss:1.028


...


train loss: 0.940 valid loss:1.003



train loss: 0.940 valid loss:1.003



train loss: 0.939 valid loss:1.003



train loss: 0.939 valid loss:1.003



train loss: 0.939 valid loss:1.002


In [52]:
count_f1_score()

0.4844150827933307

In [53]:
train(model, train_loader, valid_loader, 100, 5);

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:14: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  



train loss: 0.939 valid loss:1.003



train loss: 0.938 valid loss:1.002



train loss: 0.938 valid loss:1.002



train loss: 0.938 valid loss:1.002


...


train loss: 0.923 valid loss:0.991



train loss: 0.922 valid loss:0.991



train loss: 0.922 valid loss:0.991



train loss: 0.922 valid loss:0.991



train loss: 0.922 valid loss:0.991


In [54]:
count_f1_score()

0.49034764987636104

In [55]:
train(model, train_loader, valid_loader, 250, 5);

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:14: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  



train loss: 0.922 valid loss:0.991



train loss: 0.922 valid loss:0.991



train loss: 0.922 valid loss:0.991



train loss: 0.922 valid loss:0.991


...


train loss: 0.910 valid loss:0.984



train loss: 0.910 valid loss:0.984



train loss: 0.909 valid loss:0.984



train loss: 0.910 valid loss:0.984



train loss: 0.910 valid loss:0.984
early stopping! best valid loss: 0.9840944409370422


In [56]:
count_f1_score()

0.494337025898694

In [57]:
train(model, train_loader, valid_loader, 100, -1);

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:14: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  



train loss: 0.910 valid loss:0.984



train loss: 0.909 valid loss:0.984



train loss: 0.909 valid loss:0.984



train loss: 0.909 valid loss:0.984


...


train loss: 0.907 valid loss:0.983



train loss: 0.906 valid loss:0.983



train loss: 0.907 valid loss:0.983



train loss: 0.906 valid loss:0.983



train loss: 0.906 valid loss:0.983


In [58]:
count_f1_score()

0.49189503717335264